In [52]:
import xarray as xr
import subprocess
from datetime import datetime

def log(msg):
    print(f"[{datetime.now().strftime('%Y-%m-%d %H:%M:%S')}] {msg}")

In [59]:
cmd_pet = [
    "/home/users/fmaussion/.miniforge3/envs/spei/bin/process_climate_indices",
    "--index", "pet",
    "--periodicity", "monthly",
    "--netcdf_temp", "tmp_tas.nc",
    "--var_name_temp", "tas",
    "--output_file_base", "tmp",
    "--multiprocessing", "all",
]

cmd_spei = [
    "/home/users/fmaussion/.miniforge3/envs/spei/bin/process_climate_indices",
    "--index", "spei",
    "--periodicity", "monthly",
    "--netcdf_precip", "tmp_pr.nc",
    "--var_name_precip", "pr",
    "--netcdf_pet", "tmp_pet_thornthwaite.nc",
    "--var_name_pet", "pet_thornthwaite",
    "--output_file_base", "tmp",
    "--scales", "3", "6", "12", "24",
    "--calibration_start_year", "1981",
    "--calibration_end_year", "2010",
    "--multiprocessing", "all",
]

In [ ]:
cdir = '/home/users/fmaussion/www_fmaussion/teaching/qcr/CMIP6/'
RESs = ['075deg']  # '2deg', 

SSPs = ['ssp126', 'ssp245', 'ssp370', 'ssp585']
GCMs = ['BCC-CSM2-MR', 'CAMS-CSM1-0', 'CESM2', 'CESM2-WACCM', 
        'EC-Earth3', 'EC-Earth3-Veg', 'FGOALS-f3-L', 'GFDL-ESM4', 
        'INM-CM4-8', 'INM-CM5-0', 'MPI-ESM1-2-HR', 'MRI-ESM2-0', 
        'NorESM2-MM']

SPEIS = ["3", "6", "12", "24"]

# RESs = ['2deg']
# SSPs = ['ssp126']
# GCMs = ['BCC-CSM2-MR']
# SPEIS = ["3"]

log("=== START SPEI PROCESSING ===")
log(f"RESs = {RESs}, GCMs = {GCMs}, SSPs = {SSPs}, SPEIS = {SPEIS}")
print()

for res in RESs:
    log(f"---- Resolution: {res} ----")

    for gcm in GCMs:
        log(f"--- GCM: {gcm} ---")

        for ssp in SSPs:
            log(f"-- SSP: {ssp} --")

            f_tas =  f'{cdir}/{res}/{gcm}/{gcm}_{ssp}_regridded_tas.nc'
            f_pr =   f'{cdir}/{res}/{gcm}/{gcm}_{ssp}_regridded_pr.nc'
            of_pet = f'{cdir}/{res}/{gcm}/{gcm}_{ssp}_regridded_pet.nc'
            of_spei = f'{cdir}/{res}/{gcm}/{gcm}_{ssp}_regridded_spei.nc'

            log(f"Input TAS: {f_tas}")
            log(f"Input PR:  {f_pr}")
            log(f"Output PET: {of_pet}")
            log(f"Output SPEI: {of_spei}")

            # -----------------------------------------------------------
            # PREPARE TAS
            # -----------------------------------------------------------
            log("Reading TAS → tmp_tas.nc ...")
            with xr.open_dataset(f_tas) as ds:
                save_lat = ds['latitude']
                save_enc_tas = ds['tas'].encoding
                ds = ds.rename({'latitude':'lat', 'longitude':'lon'})
                ds['lat'] = ds['lat'].clip(-90+0.00001, 90-0.000001)
                ds['tas'] = ds['tas'].transpose('lat', 'lon', 'time')
                ds.to_netcdf('tmp_tas.nc')
            log("Wrote tmp_tas.nc")

            log("Running PET computation ...")
            try:
                subprocess.run(cmd_pet, check=True, capture_output=True)
            except subprocess.CalledProcessError as e:
                log("ERROR: PET computation failed!")
                log(e.stderr.decode())
                raise
            log("PET finished.")

            # -----------------------------------------------------------
            # PREPARE PR
            # -----------------------------------------------------------
            log("Reading PR → tmp_pr.nc ...")
            with xr.open_dataset(f_pr) as ds:
                save_lat = ds['latitude']
                save_enc_pr = ds['pr'].encoding
                ds = ds.rename({'latitude':'lat', 'longitude':'lon'})
                ds['lat'] = ds['lat'].clip(-90+0.00001, 90-0.000001)
                ds['pr'] = ds['pr'].transpose('lat', 'lon', 'time') * ds['time.days_in_month'] * 60 * 60 * 24
                ds['pr'].attrs['units'] = 'mm'
                ds.to_netcdf('tmp_pr.nc')
            log("Wrote tmp_pr.nc")

            log("Running SPEI computation ...")
            try:
                subprocess.run(cmd_spei, check=True, capture_output=True)
            except subprocess.CalledProcessError as e:
                log("ERROR: PET computation failed!")
                log(e.stderr.decode())
                raise
            log("SPEI finished.")

            # -----------------------------------------------------------
            # SAVE PET
            # -----------------------------------------------------------
            log("Writing final PET file ...")
            with xr.open_dataset('tmp_pet_thornthwaite.nc') as ds:
                ds = ds.load()
                ds['pet_thornthwaite'] = ds['pet_thornthwaite'].transpose('time', 'lat', 'lon')
                ds = ds.rename({'lat':'latitude', 'lon':'longitude'})
                ds['latitude'] = save_lat
                
                for key in ['source', 'szip', 'zstd', 'bzip2', 'blosc', 'coordinates', 'preferred_chunks']:
                    save_enc_tas.pop(key, None)
                    
                enc = {'pet_thornthwaite': save_enc_tas}
                ds.to_netcdf(of_pet, encoding=enc)

            log(f"Saved PET → {of_pet}")

            # -----------------------------------------------------------
            # SAVE SPEI
            # -----------------------------------------------------------
            log("Writing final SPEI file ...")

            for key in ['source', 'szip', 'zstd', 'bzip2', 'blosc', 'coordinates', 'preferred_chunks']:
                save_enc_pr.pop(key, None)

            enc = {}
            varname = f'spei_pearson_{int(SPEIS[0]):02d}'

            log(f"Reading SPEI {SPEIS[0]} ...")
            with xr.open_dataset(f'tmp_{varname}.nc') as ds:
                ds = ds.load()
                ds[varname] = ds[varname].transpose('time', 'lat', 'lon')
                ds = ds.rename({'lat':'latitude', 'lon':'longitude'})
                ds['latitude'] = save_lat
                enc[varname] = save_enc_pr

            # Add others if any
            for spei in SPEIS[1:]:
                varname = f'spei_pearson_{int(spei):02d}'
                log(f"Reading additional SPEI {spei} ...")

                with xr.open_dataset(f'tmp_{varname}.nc') as tds:
                    tds = tds.load()
                    tds[varname] = tds[varname].transpose('time', 'lat', 'lon')
                    tds = tds.rename({'lat':'latitude', 'lon':'longitude'})
                    tds['latitude'] = save_lat
                    ds[varname] = tds[varname]
                    enc[varname] = save_enc_pr
            
            ds.to_netcdf(of_spei, encoding=enc)
            log(f"Saved SPEI → {of_spei}")

log("=== ALL DONE ===")

[2025-11-27 00:11:24] === START SPEI PROCESSING ===
[2025-11-27 00:11:24] RESs = ['2deg'], GCMs = ['BCC-CSM2-MR'], SSPs = ['ssp126'], SPEIS = ['3']

[2025-11-27 00:11:24] ---- Resolution: 2deg ----
[2025-11-27 00:11:24] --- GCM: BCC-CSM2-MR ---
[2025-11-27 00:11:24] -- SSP: ssp126 --
[2025-11-27 00:11:24] Input TAS: /home/users/fmaussion/www_fmaussion/teaching/qcr/CMIP6//2deg/BCC-CSM2-MR/BCC-CSM2-MR_ssp126_regridded_tas.nc
[2025-11-27 00:11:24] Input PR:  /home/users/fmaussion/www_fmaussion/teaching/qcr/CMIP6//2deg/BCC-CSM2-MR/BCC-CSM2-MR_ssp126_regridded_pr.nc
[2025-11-27 00:11:24] Output PET: /home/users/fmaussion/www_fmaussion/teaching/qcr/CMIP6//2deg/BCC-CSM2-MR/BCC-CSM2-MR_ssp126_regridded_pet.nc
[2025-11-27 00:11:24] Output SPEI: /home/users/fmaussion/www_fmaussion/teaching/qcr/CMIP6//2deg/BCC-CSM2-MR/BCC-CSM2-MR_ssp126_regridded_spei.nc
[2025-11-27 00:11:24] Reading TAS → tmp_tas.nc ...
[2025-11-27 00:11:26] Wrote tmp_tas.nc
[2025-11-27 00:11:26] Running PET computation ...
[202